# Watershed on a mesh

The notebook uses [igl](https://libigl.github.io/libigl-python-bindings/) and [higra](https://higra.readthedocs.io/en/stable/index.html). The viewer used in this notebook is [meshplot](https://skoch9.github.io/meshplot/meshplot_docs/).

We are going to read a mesh file, compute a curvature measure on the mesh, and compute a watershed on the dual graph of the mesh.

Reference paper:
> Jean Cousty,  Gilles Bertrand,  Michel Couprie,  Laurent Najman
> Collapses and watersheds in pseudomanifolds of arbitrary dimension.
> Journal of Mathematical Imaging and Vision volume 50, pages 261–285 (2014) [10.1007/s10851-014-0498-z](https://doi.org/10.1007/s10851-014-0498-z). [hal-00871498v2](https://hal.science/hal-00871498/)

For an application of the hierarchical  watershed on a mesh, you can look at:

> Sylvie Philipp-Foliguet, Michel M. Jordan, Laurent Najman, Jean Cousty. 
> Artwork 3D model database indexing and classification. 
> Pattern Recognition, 2011, 44 (3), pp.588-597.  [10.1016/j.patcog.2010.09.016](https://doi.org/10.1016/j.patcog.2010.09.016). [hal-00538470](https://hal.science/hal-00538470/)




In [1]:
# Are we using google colab ? The answer is IN_COLAB
import sys
import subprocess # Needed later for checking pip modules
IN_COLAB = 'google.colab' in sys.modules

After installing colab (next cell), the execution of the notebook will likely restart. You can restart everything safely and run all cells, this cell will not be executed twice.

In [2]:
# Installing conda on colab will restart the notebook
# An error is raised by colab, that you can safely ignore it
if IN_COLAB:
  #Get the list of installed modules
  modules = subprocess.run(['pip', 'list'], stdout=subprocess.PIPE).stdout.decode('utf-8')
  if 'conda' not in modules: # Install condacolab only once
    !pip install -q condacolab
    import condacolab
    condacolab.install()
  else:
    print('Conda is already installed')

Conda is already installed


Installing the required packages requires some time. Be patient!

In [3]:
#Get the list of installed modules
modules = subprocess.run(['pip', 'list'], stdout=subprocess.PIPE).stdout.decode('utf-8')

In [4]:
%%capture
# Checking if the required modules are installed (and install them if not)
if 'igl' not in modules:
  !conda install -c conda-forge igl
if 'meshplot' not in modules:
  !conda install -c conda-forge meshplot
if 'higra' not in modules:
  !pip install higra

We are working with the complete bunny model.

In [5]:
!wget 'https://raw.githubusercontent.com/higra/Higra-Notebooks/master/data/BunnyStanford.obj'

--2023-01-26 10:30:22--  https://raw.githubusercontent.com/higra/Higra-Notebooks/master/data/BunnyStanford.obj
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.109.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3003441 (2.9M) [text/plain]
Saving to: ‘BunnyStanford.obj.1’

BunnyStanford.obj.1 100%[===================>]   2.86M  --.-KB/s    in 0.07s   

2023-01-26 10:30:23 (43.2 MB/s) - ‘BunnyStanford.obj.1’ saved [3003441/3003441]



In [6]:
import igl
from meshplot import plot, subplot, interact
import meshplot as mp
import higra as hg
import numpy as np
import scipy as sp

In [7]:
# Use offline version, plus html output
mp.offline() # On colab, meshplot has some issue
from IPython.display import display, HTML # that we correct with HTML

In [8]:
v, _, n, f, _, _ =igl.read_obj('./BunnyStanford.obj')

In [9]:
#Compute some curvature measures

#First, Gaussian curvature
k = igl.gaussian_curvature(v, f)

# Next, compute the massmatrix and divide the gaussian curvature values by area to get the integral average.
m = igl.massmatrix(v, f, igl.MASSMATRIX_TYPE_VORONOI)
minv = sp.sparse.diags(1 / m.diagonal())
kn = minv.dot(k)

# Then, the mean curvature
l = igl.cotmatrix(v, f)
m = igl.massmatrix(v, f, igl.MASSMATRIX_TYPE_VORONOI)

minv = sp.sparse.diags(1 / m.diagonal())

hn = -minv.dot(l.dot(v))
h = np.linalg.norm(hn, axis=1)

In [10]:
# Choose a curvature, either k or kn, or h 
curv = h

In [11]:
display(HTML(plot(v, f, np.log(curv)).to_html()))

Plot saved to file 7b188647-8b9a-450d-879f-c3eaf98b4de0.html.


In [12]:
#Helper function
def dual_graph(F):
  #Input: a set of faces
  #Return: the dual graph of the faces
  # in the form (source, dest, edgeverticesid)
  # edgeverticesid[i] is the indices of the point forming edge i

  #FE #F by #3 adjacent matrix, the element i,j is the id of the triangle
  #  adjacent to the j edge of triangle i
  #EF #F by #3 adjacent matrix, the element i,j is the id of edge of the
  #  triangle FE(i,j) that is adjacent with triangle i  
  # EF is not used here.
  FE,EF = igl.triangle_triangle_adjacency(F)
  source = np.repeat(np.arange(FE.shape[0]), FE.shape[1])
  dest = FE.ravel()
  # edgeid is the id of the points of F
  edgeid = np.arange(F.shape[1]) + np.zeros(F.shape)
  edgeid = edgeid.ravel().astype(int)

  # Remove duplicated edges and -1 neighbors
  filt = (dest > source) # & (dest > -1) is not needed
  source = source[filt]
  dest = dest[filt]
  edgeid = edgeid[filt]

  # Find the indices of the point forming the edge
  matchedgeid = { 
    #From the igl doc: 
    #     The first edge of a triangle is [0,1] 
    #     The second [1,2] and the third [2,3==0].
    -1: [-1,-1],  # Should not happen, but here for completion
    0: [0,1],
    1: [1,2],
    2: [2,0]
  }
  # We apply matchedgeid on each element of edgeid
  # The following is faster than a vectorized version
  # because u is very small (3 values)
  u,inv = np.unique(edgeid,return_inverse = True)
  fi = np.array([matchedgeid[x] for x in u])[inv]
  # source[i] is the face i
  # and (F[source[i], fi[i,0]], F[source[i], fi[i,0]]) are the indices of 
  #      the two points of the mesh
  #      forming the edge (source[i], dest[i])
  #      ie, the edge between F[source[i]] and F[FE[i]]
  edgeverticesid=np.stack([F[source, fi[:,0]], F[source, fi[:,1]]], axis=1)

  return source, dest, edgeverticesid

In [13]:
# Build Higra graph
sources, dest, edgevid = dual_graph(f)
g = hg.UndirectedGraph(f.shape[0]) # Number of points is the number of faces in the mesh
g.add_edges(sources, dest)

In [14]:
print(np.array(edgevid).shape)

(105558, 2)


In [15]:
# Weight the edges
eg = np.array(edgevid)
edge_weights = (curv[eg[:,0]] + curv[eg[:,1]])/2.

In [16]:
# Compute the hierarchy
area = igl.doublearea(v,f)/2. # Area of the faces
tree, altitudes = hg.watershed_hierarchy_by_area(g, edge_weights, area)
#tree, altitudes = hg.binary_partition_tree_single_linkage(g, edge_weights)

In [17]:
# Compute the saliency map
sal = hg.saliency(tree, altitudes)

In [18]:
np.unique(sal).shape

(16388,)

In [19]:
# Number of level of the saliency map to show
salLevel = 200

In [20]:
shading = {"flat":True, # Flat or smooth shading of triangles
           "wireframe":False, "wire_width": 0.03, "wire_color": "black", # Wireframe rendering
           "width": 600, "height": 600, # Size of the viewer canvas
           "antialias": True, # Antialising, might not work on all GPUs
           "scale": 2.0, # Scaling of the model
           "side": "DoubleSide", # FrontSide, BackSide or DoubleSide rendering of the triangles
           "colormap": "viridis", "normalize": [None, None], # Colormap and normalization for colors
           "background": "#ffffff", # Background color of the canvas
           "line_width": 1.0, "line_color": "black", # Line properties of overlay lines
           "bbox": False, # Enable plotting of bounding box
           "point_color": "red", "point_size": 0.01 # Point properties of overlay points
          }

p=plot(v, f, c=np.array([.5,.5,.5]), shading=shading)
 
salcol = np.unique(sal)
if salcol.shape[0]<salLevel:
  salLevel = salcol.shape[0]
salcol = salcol[-salLevel:] # Last salLevel levels of saliency map
col = mp.utils.get_colors(np.unique(salcol), colormap='binary_r')
col = col*255
col = col.astype(int)
for i in range(salLevel):
  sal_edges = eg[sal == salcol[i]]
  strcol = 'rgb({0},{1},{2})'.format(col[i][0], col[i][1], col[i][2])
  p.add_lines(v[sal_edges[:,0]], v[sal_edges[:,1]], shading={"line_color": strcol, "line_width": 3.0})
display(HTML(p.to_html()))

Plot saved to file c972865b-689e-46db-bbb8-f39b94fd37b0.html.


In [21]:
p.save("bunnyWatershed.html")

Plot saved to file bunnyWatershed.html.
